In [4]:
import pandas as pd
from matplotlib.figure import Figure

df = pd.read_csv("../src_data/eval_results.csv")
df

runname   steps  agg_score  commonsense_qa/acc  \
0           C4       0   0.330893               0.186   
1           C4    1000   0.355112               0.229   
2           C4    2000   0.378435               0.268   
3           C4    3000   0.387795               0.280   
4           C4    4000   0.399320               0.296   
...        ...     ...        ...                 ...   
1171  The Pile  163000   0.463789               0.379   
1172  The Pile  164000   0.462758               0.369   
1173  The Pile  165000   0.465026               0.383   
1174  The Pile  166000   0.462349               0.377   
1175  The Pile  167000   0.464539               0.386   

      commonsense_qa/acc_norm  hellaswag/acc  hellaswag/acc_norm  \
0                       0.233          0.272               0.258   
1                       0.260          0.286               0.288   
2                       0.278          0.312               0.330   
3                       0.295          0.331               0.380   
4                       0.298          0.351               0.406   
...                       ...            ...                 ...   
1171                    0.349          0.441               0.555   
1172                    0.344          0.438               0.552   
1173                    0.350          0.438               0.553   
1174                    0.346          0.440               0.557   
1175                    0.354          0.434               0.557   

      openbookqa/acc  openbookqa/acc_norm  piqa/acc  ...  siqa/acc  \
0              0.166                0.286     0.542  ...     0.367   
1              0.128                0.250     0.614  ...     0.351   
2              0.122                0.276     0.646  ...     0.375   
3              0.152                0.274     0.660  ...     0.376   
4              0.168                0.282     0.676  ...     0.382   
...              ...                  ...       ...  ...       ...   
1171           0.240                0.366     0.701  ...     0.405   
1172           0.248                0.348     0.708  ...     0.395   
1173           0.234                0.352     0.707  ...     0.400   
1174           0.228                0.346     0.711  ...     0.398   
1175           0.232                0.356     0.706  ...     0.402   

      siqa/acc_norm  winogrande/acc  winogrande/acc_norm  sciq/acc  \
0             0.362           0.516                0.497     0.208   
1             0.404           0.519                0.476     0.565   
2             0.400           0.509                0.500     0.676   
3             0.387           0.512                0.496     0.725   
4             0.404           0.522                0.503     0.723   
...             ...             ...                  ...       ...   
1171          0.388           0.585                0.560     0.875   
1172          0.401           0.577                0.567     0.874   
1173          0.401           0.569                0.556     0.874   
1174          0.398           0.572                0.558     0.877   
1175          0.402           0.573                0.559     0.867   

      sciq/acc_norm  arc/acc  arc/acc_norm  mmlu/acc  mmlu/acc_norm  
0             0.202   0.2195        0.2510  0.230294       0.250147  
1             0.518   0.2680        0.2935  0.238951       0.250399  
2             0.577   0.3065        0.3230  0.247275       0.255482  
3             0.621   0.3175        0.3340  0.254534       0.267363  
4             0.618   0.3255        0.3470  0.254762       0.263563  
...             ...      ...           ...       ...            ...  
1171          0.820   0.4475        0.4450  0.299378       0.326313  
1172          0.806   0.4465        0.4355  0.302083       0.331563  
1173          0.811   0.4460        0.4455  0.305193       0.331708  
1174          0.811   0.4525        0.4385  0.301952       0.331295  
1175          0.802   0.4475        0.4375  0.301934 

In [5]:
import json
import os
from matplotlib import pyplot as plt
metrics = ['agg_score', 'commonsense_qa/acc_norm', 'hellaswag/acc_norm', 'openbookqa/acc_norm', 'piqa/acc_norm',
                   'siqa/acc_norm', 'winogrande/acc_norm', 'arc/acc_norm', 'mmlu/acc_norm']

def normalize_runname(runname):
    return runname.replace("/", "_")

grouped = (
    df.groupby(["runname", "steps"])
    .agg(
        {
            key: "mean" for key in metrics
        }
    )
    .reset_index()
)

file_id="../assets/data/plots/dataset_ablations"
files = {}
for metric in metrics:
    datas = {}
    for name, group in grouped.groupby("runname"):
        group = group[["steps", metric]].sort_values(by="steps")
        group = group.set_index("steps")
        rolling_avg = group
        # rolling_avg = group.rolling(window=5).mean()
        datas[name] = {
            "x": (rolling_avg.index * 2048 * 1024 * 1e-9).tolist(),
            "y": rolling_avg[metric].tolist(),
            "label": name,
        }
    # Sort the datata based on the steps
    datas = {k: v for k, v in sorted(datas.items(), key=lambda x: -x[1]["y"][-1])}
    # Create a folder
    os.makedirs(f"{file_id}", exist_ok=True)
    with open(f"{file_id}/{normalize_runname(metric)}.json", "w") as f:
        json.dump({
            "data": datas,
            "layout": {
                "title": {
                    "text": "Dataset ablations"
                },
            }
        }, f)
    files[metric] = {"file": f"{normalize_runname(metric)}.json"}
# Create index
with open(f"{file_id}/index.json", "w") as f:
    json.dump({
        "files": files,
        "settings": {
            "defaultMetric": "agg_score",
            "slider":{"min":0,"max":30,"default":5}
        }
    }, f)
    